In [1]:
import pandas as pd
import numpy as np
import copy
import warnings
import plotly
import plotly.express as px
import matplotlib.pyplot as plt
import seaborn as sns
from wordcloud import WordCloud
from sklearn import metrics
from sklearn.model_selection import train_test_split
from PIL import Image 
import random
warnings.filterwarnings("ignore")
from tqdm import tqdm
import string

import torch
from torch import nn
from transformers import AutoTokenizer
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
from transformers import AutoModel, AutoModelForSequenceClassification
from transformers import DataCollatorWithPadding

In [2]:
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)

# Data

In [3]:
news = pd.read_csv('/kaggle/input/articles-updated/articles_updated.csv', sep='\t')

In [4]:
news.columns

Index(['Web', 'Title', 'Url', 'Datetime', 'Abstract', 'Unnamed: 5'], dtype='object')

In [5]:
news.head()

Web  \
0  idnes.cz   
1  idnes.cz   
2  idnes.cz   
3  idnes.cz   
4  idnes.cz   

                                                                         Title  \
0  PŘEHLEDNĚ: Co nového nás čeká v roce 2023. Za co více zaplatíme i dostaneme   
1     Česko vstoupilo do roku 2023. Zákaz pyrotechniky v centru Prahy nezabral   
2  Hodnocení skončeného předsednictví: Češi uspěli, ale neumí se tím pochlubit   
3       Kalousek má novou favoritku. Podpořil na Hrad Nerudovou místo Fischera   
4  Zeman udělil Medaili za hrdinství hasiči, který zahynul při požáru roubenky   

                                                                                                                                            Url  \
0                                                https://www.idnes.cz/zpravy/domaci/cesko-zmeny-v-roce-2023-prehledne.A221230_105559_domaci_knn   
1  https://www.idnes.cz/praha/zpravy/silvestr-novy-rok-hasici-policie-zachranna-sluzba-pripravy-vyjezdy-pyrotechnika.A221231_145404_domaci_pitt   
2                                          https://www.idnes.cz/zpravy/domaci/ceske-predsednictvi-v-rade-eu-hodnoceni.A221213_104017_domaci_knn   
3                  https://www.idnes.cz/volby/volba-prezidenta-2023-kalousek-podpora-danuse-nerudove.A230101_085308_prezidentske-volby-2023_kop   
4                             https://www.idnes.cz/zpravy/domaci/zeman-oceneni-medaile-hasic-pozar-dvorak-in-memoriam.A230101_093737_domaci_bur   

     Datetime  \
0  2023-01-01   
1  2023-01-01   
2  2023-01-01   
3  2023-01-01   
4  2023-01-01   

                                                                                                                                                                                                                                                                                                                                                       Abstract  \
0                                                                       Česko si zvolí nového prezidenta, na pražském magistrátu usedne nový primátor. Řada lidí bude muset za pohotovostí cestovat do jiného města, statisíce motoristů zase čeká výměna řidičských průkazů. To vše přinese rok 2023. Redakce iDNES.cz přináší přehledně seznam hlavních změn.   
1         Česká republika vstoupila do nového roku 2023. Oslavy se konaly na řadě míst, tradičně největší byly v centru Prahy, kde i přes zákaz došlo k odpalování pyrotechniky. Na Václavském náměstí před půlnocí muž kopl do hlavy policistu. Do druhé hodiny ranní zasahovali hasiči u padesátky požárů, záchranáři využili i specializované vozidlo Golem.   
2  Spolu s koncem roku předala Česká republika pomyslné žezlo předsednictví v Radě EU Švédsku. Tím zakončila půl rok, během kterého zodpovídala za její fungování a stála tak „v čele Evropy“. Podle odborníků i politiků, které redakce iDNES.cz oslovila, země v této zkoušce obstála. Úspěchy jsou ale málo vidět a vláda je nedokázala dostatečně „prodat“.   
3                      Necelé dva týdny zbývají do volby nové hlavy státu a do tábora přívrženců bývalé rektorky Mendelovy univerzity v Brně Danuše Nerudové veřejně přešel bývalý ministr financí a expředseda TOP 09 Miroslav Kalousek. Dosud přitom podporoval senátora Pavla Fischera, který ale podle Kalouska nemá šanci na postup do druhého kola volby.   
4                                                                                                                                                                                          Prezident Miloš Zeman udělil Medaili za hrdinství in memoriam Janu Dvořákovi. Dobrovolný hasič zahynul v listopadu při požáru roubenky v Novém Boru - Arnultovicích.   

  Unnamed: 5  
0        NaN  
1        NaN  
2        NaN  
3        NaN  
4        NaN

# Preproc

In [6]:
news[~news['Unnamed: 5'].isna()]

Web  \
2603            ac24.cz   
2774  czechfreepress.cz   

                                                                Title  \
2603           Počet mrtvých při útoku na dněperský byt vzrostl na 44   
2774  BKP: Profesionální lež – nástroj autogenocidy jedince i lidstva   

                                                                                                                  Url  \
2603                                                                                    poradce Zelenského rezignoval   
2774  https://www.czechfreepress.cz//vase-free-zona/bkp-profesionalni-lez-nastroj-autogenocidy-jedince-i-lidstva.html   

                                                                                                                       Datetime  \
2603  https://www.ac24.cz/zpravy-ze-sveta/pocet-mrtvych-pri-utoku-na-dnepersky-byt-vzrostl-na-44-zelenskeho-poradce-rezignoval/   
2774                                                                                                                 2023-01-16   

                                                                                         Abstract  \
2603                                                                                   2023-01-17   
2774  „Ďábel je lhář a vrah.“ (J 8,44) „A není divu, vždyť sám satan se převléká za anděla světla   

                                                                                                                                                                                                                                                                                                                                                                                                                                               Unnamed: 5  
2603                                                                                                                                                                                                                                                           Počet obětí útoku na byt v Dněpru, k němuž došlo v sobotu odpoledne, kdy se odehrávaly poslední víkendové ruské letecké útoky proti ukrajinské energetické infrastruktuře. (Foto: Twitter)  
2774  není tedy nic překvapujícího na tom, že se jeho služebníci převlékají za služebníky spravedlnosti. Jejich konec bude jako jejich skutky!“ (2Kor 11,14-15) Čeká je Peklo pak budou psi a čarodějníci, smilníci, vrahové a modláři i každý, kdo miluje a činí lež.“ (Zj 22,15)Komu slouží internet, google, sociální sítě, masmédia? Duchu pravdy, anebo duchu lži? Tvůrci sociálních médií se vyjádřili, že publikovat pravdu je prý pro lidi nudné.

In [7]:
print('The number of articles before processing :',len(news))
news = news[news['Unnamed: 5'].isna()]
print('The number of articles after processing :',len(news))

The number of articles before processing : 2792
The number of articles after processing : 2790


In [8]:
news[news["Abstract"].isna()]

Web  \
328   Řekl to v neděli v pořadu České televize Otázky Václava Moravce. V polovině prosince uvedl i sám prezident, že amnestii do konce svého mandátu nevyhlásí. K vyhlášení amnestie na rozdíl od prezidentské milosti by potřeboval spolupodepsání premiérem.   
526                                                                                                                    V tajné volbě Svatoně podpořilo 57 z 68 přítomných senátorů. „Chtěl bych velmi poděkovat za projevenou důvěru,“ řekl po zvolení Svatoň.   
708                                                           Pronajímatel má ze zákona právo na jednostranné zvýšení nájemného za pronájem bytu. Při zvyšování musí však být dodrženy zákonné podmínky, jakož i případná ujednání obsažená v nájemní smlouvě.   
1251  Řekl to v neděli v pořadu České televize Otázky Václava Moravce. V polovině prosince uvedl i sám prezident, že amnestii do konce svého mandátu nevyhlásí. K vyhlášení amnestie na rozdíl od prezidentské milosti by potřeboval spolupodepsání premiérem.   
1474                                                                                                                                                                                                                                                lidovky.cz   
1475                                                                                                                                                                                                                                                lidovky.cz   
1731                                                                                                                   V tajné volbě Svatoně podpořilo 57 z 68 přítomných senátorů. „Chtěl bych velmi poděkovat za projevenou důvěru,“ řekl po zvolení Svatoň.   
2201                                                                                                                                                                                                                                               aktualne.cz   
2202                                                                                                                                                                                                                                                       NaN   
2369                                                                                                                                                                                                                                               aktualne.cz   
2370                                                                                                                                                                                                                                                       NaN   

                                              Title  \
328                                             NaN   
526                                             NaN   
708                                             NaN   
1251                                            NaN   
1474  Hlásíte se z páté třídy na víceleté gymnázium   
1475     Hlásíte se z deváté třídy na střední školu   
1731                                            NaN   
2201                                           ŽIVĚ   
2202                                            NaN   
2369                                           ŽIVĚ   
2370                                            NaN   

                                                                                                                               Url  \
328                                                                                                                            NaN   
526                                                                                                                            NaN   
708                                                                                        

In [9]:
print('the number of articles before processing :',len(news))
news = news.dropna(subset=['Abstract'])
print('The number of articles after processing :',len(news))

the number of articles before processing : 2790
The number of articles after processing : 2779


In [10]:
duplicate_rows = news[news.duplicated()]
print("Duplicate Rows:")
print(duplicate_rows)

Duplicate Rows:
                    Web                                             Title  \
2773  czechfreepress.cz  Za našimi zády se dějí věci, je to smutné čtení…   

                                                                                              Url  \
2773  https://www.czechfreepress.cz//politika/za-nasimi-zady-se-deji-veci-je-to-smutne-cteni.html   

        Datetime  \
2773  2023-01-15   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               Abstract  \
2773  Zatímco veřejnost se zabývá prezidentskými volbami, Pětikoalice v jejich stínu usilovně 

In [11]:
print('The number of articles before processing :',len(news))
news = news.drop_duplicates()
print('The number of articles after processing :',len(news))

The number of articles before processing : 2779
The number of articles after processing : 2778


In [12]:
news.reset_index(drop=True, inplace=True)

In [13]:
news = news.drop('Unnamed: 5', axis=1)

In [14]:
news.head()

Web  \
0  idnes.cz   
1  idnes.cz   
2  idnes.cz   
3  idnes.cz   
4  idnes.cz   

                                                                         Title  \
0  PŘEHLEDNĚ: Co nového nás čeká v roce 2023. Za co více zaplatíme i dostaneme   
1     Česko vstoupilo do roku 2023. Zákaz pyrotechniky v centru Prahy nezabral   
2  Hodnocení skončeného předsednictví: Češi uspěli, ale neumí se tím pochlubit   
3       Kalousek má novou favoritku. Podpořil na Hrad Nerudovou místo Fischera   
4  Zeman udělil Medaili za hrdinství hasiči, který zahynul při požáru roubenky   

                                                                                                                                            Url  \
0                                                https://www.idnes.cz/zpravy/domaci/cesko-zmeny-v-roce-2023-prehledne.A221230_105559_domaci_knn   
1  https://www.idnes.cz/praha/zpravy/silvestr-novy-rok-hasici-policie-zachranna-sluzba-pripravy-vyjezdy-pyrotechnika.A221231_145404_domaci_pitt   
2                                          https://www.idnes.cz/zpravy/domaci/ceske-predsednictvi-v-rade-eu-hodnoceni.A221213_104017_domaci_knn   
3                  https://www.idnes.cz/volby/volba-prezidenta-2023-kalousek-podpora-danuse-nerudove.A230101_085308_prezidentske-volby-2023_kop   
4                             https://www.idnes.cz/zpravy/domaci/zeman-oceneni-medaile-hasic-pozar-dvorak-in-memoriam.A230101_093737_domaci_bur   

     Datetime  \
0  2023-01-01   
1  2023-01-01   
2  2023-01-01   
3  2023-01-01   
4  2023-01-01   

                                                                                                                                                                                                                                                                                                                                                       Abstract  
0                                                                       Česko si zvolí nového prezidenta, na pražském magistrátu usedne nový primátor. Řada lidí bude muset za pohotovostí cestovat do jiného města, statisíce motoristů zase čeká výměna řidičských průkazů. To vše přinese rok 2023. Redakce iDNES.cz přináší přehledně seznam hlavních změn.  
1         Česká republika vstoupila do nového roku 2023. Oslavy se konaly na řadě míst, tradičně největší byly v centru Prahy, kde i přes zákaz došlo k odpalování pyrotechniky. Na Václavském náměstí před půlnocí muž kopl do hlavy policistu. Do druhé hodiny ranní zasahovali hasiči u padesátky požárů, záchranáři využili i specializované vozidlo Golem.  
2  Spolu s koncem roku předala Česká republika pomyslné žezlo předsednictví v Radě EU Švédsku. Tím zakončila půl rok, během kterého zodpovídala za její fungování a stála tak „v čele Evropy“. Podle odborníků i politiků, které redakce iDNES.cz oslovila, země v této zkoušce obstála. Úspěchy jsou ale málo vidět a vláda je nedokázala dostatečně „prodat“.  
3                      Necelé dva týdny zbývají do volby nové hlavy státu a do tábora přívrženců bývalé rektorky Mendelovy univerzity v Brně Danuše Nerudové veřejně přešel bývalý ministr financí a expředseda TOP 09 Miroslav Kalousek. Dosud přitom podporoval senátora Pavla Fischera, který ale podle Kalouska nemá šanci na postup do druhého kola volby.  
4                                                                                                                                                                                          Prezident Miloš Zeman udělil Medaili za hrdinství in memoriam Janu Dvořákovi. Dobrovolný hasič zahynul v listopadu při požáru roubenky v Novém Boru - Arnultovicích.

# Tokenizace

In [15]:
bert_uncased_tokenizer = AutoTokenizer.from_pretrained("bert-base-uncased")

tokenizer_config.json:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

In [16]:
class BertBaseDataset(Dataset):
    def __init__(self, tokenizer, df, text_col, max_len):
        self.tokenizer = tokenizer
        self.texts = df[text_col].values.tolist()
        self.max_len = max_len

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, idx):
        res = self.tokenizer(
            self.texts[idx],
            return_tensors="pt",
            padding=False,
            truncation=True,
            # return_special_tokens_mask=True,
            max_length=self.max_len,
        )
        res = {k:v[0] for k,v in res.items()}
        return res
    
def dynamic_pad_data_loader(tokenizer, dataset, batch_size, shuffle):
    data_collator = DataCollatorWithPadding(tokenizer=tokenizer)
    
    return DataLoader(
        dataset,
        batch_size=batch_size,
        shuffle=shuffle,
        collate_fn=data_collator
    )

In [17]:
backbone = "nlptown/bert-base-multilingual-uncased-sentiment"
tokenizer = AutoTokenizer.from_pretrained(backbone)

ds = BertBaseDataset(tokenizer, news, "Abstract", None)
dl = dynamic_pad_data_loader(tokenizer, ds, batch_size=32, shuffle=False)

tokenizer_config.json:   0%|          | 0.00/39.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/953 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/872k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

# Sentiment Analyza

In [18]:
model = AutoModelForSequenceClassification.from_pretrained(backbone)
model.eval()

preds = []

with torch.no_grad(), tqdm(total=len(dl)) as pbar:
    for batch in dl:
        output = model(**batch)
        preds.append(output["logits"])
        pbar.update(1)

# Concatenate the logits from all batches
preds = torch.cat(preds, dim=0)

print("Shape of all logits:", preds.shape)

pytorch_model.bin:   0%|          | 0.00/669M [00:00<?, ?B/s]

100%|██████████| 87/87 [10:25<00:00,  7.19s/it]

Shape of all logits: torch.Size([2778, 5])


# Vysledky

In [19]:
preds = preds.softmax(1).numpy()
preds_df = pd.DataFrame(preds, columns=[f"{i+1} stars" for i in range(5)])
preds_df["predicted stars"] = preds.argmax(axis=1) + 1
preds_df.insert(0, "Title", news['Title'])
preds_df.insert(0, "Abstract", news["Abstract"])
preds_df.insert(0, "Datetime", news["Datetime"])
preds_df.insert(0, 'Web', news['Web'])
preds_df.head()

Web    Datetime  \
0  idnes.cz  2023-01-01   
1  idnes.cz  2023-01-01   
2  idnes.cz  2023-01-01   
3  idnes.cz  2023-01-01   
4  idnes.cz  2023-01-01   

                                                                                                                                                                                                                                                                                                                                                       Abstract  \
0                                                                       Česko si zvolí nového prezidenta, na pražském magistrátu usedne nový primátor. Řada lidí bude muset za pohotovostí cestovat do jiného města, statisíce motoristů zase čeká výměna řidičských průkazů. To vše přinese rok 2023. Redakce iDNES.cz přináší přehledně seznam hlavních změn.   
1         Česká republika vstoupila do nového roku 2023. Oslavy se konaly na řadě míst, tradičně největší byly v centru Prahy, kde i přes zákaz došlo k odpalování pyrotechniky. Na Václavském náměstí před půlnocí muž kopl do hlavy policistu. Do druhé hodiny ranní zasahovali hasiči u padesátky požárů, záchranáři využili i specializované vozidlo Golem.   
2  Spolu s koncem roku předala Česká republika pomyslné žezlo předsednictví v Radě EU Švédsku. Tím zakončila půl rok, během kterého zodpovídala za její fungování a stála tak „v čele Evropy“. Podle odborníků i politiků, které redakce iDNES.cz oslovila, země v této zkoušce obstála. Úspěchy jsou ale málo vidět a vláda je nedokázala dostatečně „prodat“.   
3                      Necelé dva týdny zbývají do volby nové hlavy státu a do tábora přívrženců bývalé rektorky Mendelovy univerzity v Brně Danuše Nerudové veřejně přešel bývalý ministr financí a expředseda TOP 09 Miroslav Kalousek. Dosud přitom podporoval senátora Pavla Fischera, který ale podle Kalouska nemá šanci na postup do druhého kola volby.   
4                                                                                                                                                                                          Prezident Miloš Zeman udělil Medaili za hrdinství in memoriam Janu Dvořákovi. Dobrovolný hasič zahynul v listopadu při požáru roubenky v Novém Boru - Arnultovicích.   

                                                                         Title  \
0  PŘEHLEDNĚ: Co nového nás čeká v roce 2023. Za co více zaplatíme i dostaneme   
1     Česko vstoupilo do roku 2023. Zákaz pyrotechniky v centru Prahy nezabral   
2  Hodnocení skončeného předsednictví: Češi uspěli, ale neumí se tím pochlubit   
3       Kalousek má novou favoritku. Podpořil na Hrad Nerudovou místo Fischera   
4  Zeman udělil Medaili za hrdinství hasiči, který zahynul při požáru roubenky   

    1 stars   2 stars   3 stars   4 stars   5 stars  predicted stars  
0  0.088154  0.072447  0.159511  0.369156  0.310732                4  
1  0.213713  0.120329  0.124306  0.232894  0.308758                5  
2  0.317008  0.359434  0.207930  0.082485  0.033143                2  
3  0.448963  0.300542  0.145913  0.072200  0.032383                1  
4  0.205436  0.065649  0.127099  0.260190  0.341625                5

In [20]:
len(preds_df)

2778

In [21]:
preds_df

Web    Datetime  \
0              idnes.cz  2023-01-01   
1              idnes.cz  2023-01-01   
2              idnes.cz  2023-01-01   
3              idnes.cz  2023-01-01   
4              idnes.cz  2023-01-01   
5              idnes.cz  2023-01-01   
6              idnes.cz  2023-01-01   
7              idnes.cz  2023-01-01   
8              idnes.cz  2023-01-01   
9              idnes.cz  2023-01-01   
10             idnes.cz  2023-01-01   
11             idnes.cz  2023-01-01   
12             idnes.cz  2023-01-01   
13             idnes.cz  2023-01-01   
14             idnes.cz  2023-01-01   
15             idnes.cz  2023-01-01   
16             idnes.cz  2023-01-01   
17             idnes.cz  2023-01-01   
18             idnes.cz  2023-01-01   
19             idnes.cz  2023-01-01   
20             idnes.cz  2023-01-02   
21             idnes.cz  2023-01-02   
22             idnes.cz  2023-01-02   
23             idnes.cz  2023-01-02   
24             idnes.cz  2023-01-02   
25             idnes.cz  2023-01-02   
26             idnes.cz  2023-01-02   
27             idnes.cz  2023-01-02   
28             idnes.cz  2023-01-02   
29             idnes.cz  2023-01-02   
30             idnes.cz  2023-01-02   
31             idnes.cz  2023-01-02   
32             idnes.cz  2023-01-02   
33             idnes.cz  2023-01-02   
34             idnes.cz  2023-01-02   
35             idnes.cz  2023-01-02   
36             idnes.cz  2023-01-02   
37             idnes.cz  2023-01-02   
38             idnes.cz  2023-01-02   
39             idnes.cz  2023-01-02   
40             idnes.cz  2023-01-03   
41             idnes.cz  2023-01-03   
42             idnes.cz  2023-01-03   
43             idnes.cz  2023-01-03   
44             idnes.cz  2023-01-03   
45             idnes.cz  2023-01-03   
46             idnes.cz  2023-01-03   
47             idnes.cz  2023-01-03   
48             idnes.cz  2023-01-03   
49             idnes.cz  2023-01-03   
50             idnes.cz  2023-01-03   
51             idnes.cz  2023-01-03   
52             idnes.cz  2023-01-03   
53             idnes.cz  2023-01-03   
54             idnes.cz  2023-01-04   
55             idnes.cz  2023-01-04   
56             idnes.cz  2023-01-04   
57             idnes.cz  2023-01-04   
58             idnes.cz  2023-01-04   
59             idnes.cz  2023-01-04   
60             idnes.cz  2023-01-04   
61             idnes.cz  2023-01-04   
62             idnes.cz  2023-01-04   
63             idnes.cz  2023-01-04   
64             idnes.cz  2023-01-04   
65             idnes.cz  2023-01-04   
66             idnes.cz  2023-01-04   
67             idnes.cz  2023-01-04   
68             idnes.cz  2023-01-04   
69             idnes.cz  2023-01-04   
70             idnes.cz  2023-01-04   
71             idnes.cz  2023-01-04   
72             idnes.cz  2023-01-04   
73             idnes.cz  2023-01-04   
74             idnes.cz  2023-01-04   
75             idnes.cz  2023-01-04   
76             idnes.cz  2023-01-04   
77             idnes.cz  2023-01-04   
78             idnes.cz  2023-01-04   
79             idnes.cz  2023-01-05   
80             idnes.cz  2023-01-05   
81             idnes.cz  2023-01-05   
82             idnes.cz  2023-01-05   
83             idnes.cz  2023-01-05   
84             idnes.cz  2023-01-05   
85             idnes.cz  2023-01-05   
86             idnes.cz  2023-01-05   
87             idnes.cz  2023-01-05   
88             idnes.cz  2023-01-05   
89             idnes.cz  2023-01-05   
90             idnes.cz  2023-01-05   
91             idnes.cz  2023-01-05   
92             idnes.cz  2023-01-05   
93             idnes.cz  2023-01-05   
94             idnes.cz  2023-01-05   
95             idnes.cz  2023-01-05   
96             idnes.cz  2023-01-05   
97             idnes.cz  2023-01-05   
98             idnes.cz  2023-01-05   
99             idnes.cz  2023-01-05   
100            idnes.cz  2023-01-05   
101            idnes.cz  2023-01-05   
102

In [22]:
csv_path = "/kaggle/working/preds_abstract_web_bert.csv"

# Save the DataFrame to a CSV file
preds_df.to_csv(csv_path, index=False)